In [1]:
import os
import sys

In [2]:
WORKING_FOLDER="/mnt/0060f889-4c27-409b-b0de-47f5427515e3/unicamp/ia368v_dd/trabalho_final/"
PYSERINI_FOLDER="/mnt/0060f889-4c27-409b-b0de-47f5427515e3/unicamp/ia368v_dd/pyserini/"

In [3]:
TREC_EVAL_FULLPATH=PYSERINI_FOLDER+"tools/eval/trec_eval.9.0.4/trec_eval"

os.environ["ANSERINI_CLASSPATH"]="/media/eduseiti/bigdata01/unicamp/ia368v_dd/anserini/target"

os.chdir(WORKING_FOLDER)

In [4]:
from common_tools import *

from pyserini.search.lucene import LuceneSearcher
from pyserini.analysis import get_lucene_analyzer

import glob
import numpy as np

In [5]:
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', 200)

In [6]:
BM25_INDEX_FOLDER="bm25/passage_v2"

In [7]:
CLUEWEB22_PT_CORPUS_FOLDER="clueweb22-pt_10M_sample"
CLUEWEB22_PT_TRAIN_QUERIES_FOLDER="train_queries"

CLUEWEB22_PT_STATS="10M_random_passage_v2.tsv"

In [8]:
NUMBER_OF_REFERENCE_PASSAGES=1000

### Create the train queries folder, if needed

In [9]:
if not os.path.exists(CLUEWEB22_PT_TRAIN_QUERIES_FOLDER):
    os.makedirs(CLUEWEB22_PT_TRAIN_QUERIES_FOLDER)

### Initialize OpenAI interface to use gpt-3.5-turbo

In [10]:
initialize_openai()

### Check the available Clueweb22-pt corpus parts, as prepared to ColBERT-X indexing

In [11]:
corpus_parts = sorted(glob.glob(os.path.join(CLUEWEB22_PT_CORPUS_FOLDER, "clueweb22-pt_colbertx_0*.tsv")))

In [12]:
corpus_parts

['clueweb22-pt_10M_sample/clueweb22-pt_colbertx_00.tsv',
 'clueweb22-pt_10M_sample/clueweb22-pt_colbertx_01.tsv',
 'clueweb22-pt_10M_sample/clueweb22-pt_colbertx_02.tsv',
 'clueweb22-pt_10M_sample/clueweb22-pt_colbertx_03.tsv',
 'clueweb22-pt_10M_sample/clueweb22-pt_colbertx_04.tsv']

### Read the ColBERT-X index translation, in order to access the original Clueweb22-pt indexes

This was needed since ColBERT-X original implementation only handled integer indexes for the documents.

In [13]:
index_translator = pd.read_csv(os.path.join(CLUEWEB22_PT_CORPUS_FOLDER, "clueweb22-pt_colbertx_to_clueweb_id.tsv"), 
                               sep='\t', header=None, names=['colbertx_id', 'clueweb_id'])

In [14]:
index_translator.head()

colbertx_id                   clueweb_id
0            0  clueweb22-pt0001-22-00000_1
1            1  clueweb22-pt0001-22-00001_2
2            2  clueweb22-pt0001-22-00001_3
3            3  clueweb22-pt0001-22-00001_6
4            4  clueweb22-pt0001-22-00001_7

### Read the corpus statistics

In [15]:
corpus_stats_df = pd.read_csv(os.path.join(CLUEWEB22_PT_CORPUS_FOLDER, CLUEWEB22_PT_STATS), sep='\t')

In [16]:
merged_corpus_stats_df = corpus_stats_df.merge(index_translator, left_on='id', right_on='clueweb_id')

In [17]:
merged_corpus_stats_df['bl_percentage'] = merged_corpus_stats_df['total_bl_doc_original'] / merged_corpus_stats_df['number_chrs_doc_original']

### Filter passages with no more than 3% of line breaks

In [18]:
filtered_passage_ids = merged_corpus_stats_df[merged_corpus_stats_df['bl_percentage'] <= 0.03]['colbertx_id'].to_numpy()

## Loop throught the corpus parts to sample passages and ask LLM to generate questions

In [19]:
train_queries = []

In [20]:
passages_per_part = NUMBER_OF_REFERENCE_PASSAGES // len(corpus_parts)

In [21]:
passages_per_part

200

In [26]:
for part_index, corpus_part in enumerate(corpus_parts):

    passages_df = pd.read_csv(corpus_part, sep='\t', header=None, names=['colbertx_id', 'text'])

    print("passages_df.shape={}".format(passages_df.shape))

    available_passages = np.random.permutation(passages_df.shape[0])

    
    #
    # Select a list of valid passage indexes, considering only the filtered IDs.
    #
    
    valid_passage_indexes = []

    for i in range(available_passages.shape[0]):
        passage = passages_df.iloc[available_passages[i]]

        if passage['colbertx_id'] in filtered_passage_ids:
            valid_passage_indexes.append(available_passages[i])

            if len(valid_passage_indexes) == passages_per_part:
                break
        else:
            print("Passage id={} has too many line breaks...".format(passage['colbertx_id']))
            
    print("len(valid_passage_indexes)={}\n".format(len(valid_passage_indexes)))

    for i, index in enumerate(valid_passage_indexes):
        passage = passages_df.iloc[index]

        try:
            query_creation_result = execute_LLM_query_creation(passage['text'])
        except Exception as e:
            print(e)
            
            time.sleep(5)
            
            query_creation_result = execute_LLM_query_creation(passage['text'])
            
            
        query_creation_result['passage_text'] = passage['text']
        query_creation_result['colbertx_id'] = passage['colbertx_id']
        query_creation_result['clueweb_id'] = index_translator[index_translator['colbertx_id'] == passage['colbertx_id']]['clueweb_id'].to_numpy()[0]
        query_creation_result['corpus_part_index'] = part_index

        train_queries.append(query_creation_result)
        
        if (i > 0) and (i % 10 == 0):
            pd.DataFrame(train_queries).to_csv(os.path.join(CLUEWEB22_PT_TRAIN_QUERIES_FOLDER, "generated_train_queries.tsv".format(part_index)), sep="\t", index=False)            
        
    train_queries_df = pd.DataFrame(train_queries)
    
    print("train_queries_df.shape={}\n".format(train_queries_df.shape))
    
    #
    # Save the generated queries
    #
    
    train_queries_df.to_csv(os.path.join(CLUEWEB22_PT_TRAIN_QUERIES_FOLDER, "generated_train_queries.tsv"), sep="\t", index=False)

passages_df.shape=(2000000, 2)
Passage id=1931089 has too many line breaks...
Passage id=737569 has too many line breaks...
Passage id=861979 has too many line breaks...
Passage id=122312 has too many line breaks...
Passage id=519234 has too many line breaks...
Passage id=1396065 has too many line breaks...
Passage id=252467 has too many line breaks...
Passage id=960857 has too many line breaks...
Passage id=368931 has too many line breaks...
Passage id=1389028 has too many line breaks...
Passage id=849314 has too many line breaks...
Passage id=936667 has too many line breaks...
Passage id=1163811 has too many line breaks...
Passage id=319504 has too many line breaks...
Passage id=1422102 has too many line breaks...
Passage id=82164 has too many line breaks...
Passage id=1402017 has too many line breaks...
Passage id=1824487 has too many line breaks...
Passage id=1728470 has too many line breaks...
Passage id=1929580 has too many line breaks...
Passage id=1953824 has too many line brea



Pergunta 1: Qual é o tema do fórum ou discussão?
Pergunta 2: Quais são as regras de colocação para os usuários que participam da discussão?

LLM passage queries creation duration: 2.238306999206543; cost: 0.000954


++++++++++++++++++++++++++
Passagem: "12,314-320 Although inversion of conguration takes place during normal Mitsunobu esterication most often, retention is observed during lactonization of the hindered alcohol 99 (Scheme 22), very likely through the intermediacy of an acyloxyphosphonium salt followed by acyl transfer to the alcohol.41,321 These results reported by DeShong and co-workers are of paramount importance in assigning the stereochemistry during macrolactonization involving natural product syntheses. Fleming and Ghosh had also observed retention of conguration during lactonization leading to a ve-membered ring.322 Involvement of a carbocation intermediate was invoked to explain this observation. For the preparation of S,S- and R,R-congured morpholine2,5-diones 10



Pergunta 1: Qual foi a ideia de Paul McCartney para criar um filme baseado nos Beatles?
Pergunta 2: Como os Beatles e a EMI resolveram o desafio de lançar as músicas do filme Magical Mystery Tour em um formato adequado?

LLM passage queries creation duration: 3.1772279739379883; cost: 0.001189


++++++++++++++++++++++++++
Passagem: "Suporte Fixo De Tv Para Quarto Sony Samsung LG Philco Philips Panasonic Smart Lcd Led 3d 32 43 55 508 avaliaç õesR$ 22,85 1x de R$ 22,85 sem juros no cartão de créditoSuporte Articulado Para Tvs De 15 a 43\" Full20 ELG Suportes66 avaliaç õesR$ 109,80 1x de R$ 109,80 sem juros no cartão de crédito12345678produtos relacionados à sua busca;Formas de pagamento: cartões de crédito Ame, Mastercard, Visa, Elo, American Express, Aura, Diners Club, Hipercard; boleto bancário; Ame Digital; Pix.Todas as regras e promoções são válidas apenas para produtos vendidos e entregues pela Americanas. O preço válido será o da finalização da compra. Havendo divergência, preval



Pergunta 1: Como a falta de contato físico pode afetar o desenvolvimento do sistema nervoso?
Pergunta 2: Qual é o hormônio afetado pela falta de contato físico na infância e adolescência?

LLM passage queries creation duration: 2.126950740814209; cost: 0.0011535


++++++++++++++++++++++++++
Passagem: "A biologia a serviço da dermatologia, a serviço da saúdePorque toda pele é única, a BIODERMA cuida dela com uma resposta personalizada baseada em princípios ecobiológicos. Nossas inovações e participação em avanços dermatológicos para melhorar a saúde da pele nos tornaram especialistas pioneiros em cuidados dermatológicos.Conheça todos os nossos conselhosPara lhe dar o nosso apoioGeolocalizar um ponto de vendaConheça todas as nossas ofertas e produtos numa farmácia ou parafarmácia perto da sua residência.Encontrar um ponto de vendaComprar onlineConheça todas as nossas ofertas e produtos através dos nossos parceiros, online.Comprar onlineContatoPerguntas sobre a sua pele?E-mailPontos de 



Pergunta 1: Qual é o problema que as pessoas estão enfrentando ao tentar assinar a procuração de integração com o assinadoc?
Pergunta 2: Alguma das soluções propostas pelos usuários funcionou para resolver o problema de assinatura digital?

LLM passage queries creation duration: 2.880607843399048; cost: 0.001336


++++++++++++++++++++++++++
Passagem: "Referências↑ « A Pantera Cor-de-Rosa ». no AdoroCinema↑ «A Pantera Côr de Rosa». SAPO Mag. Portugal. Consultado em 2 de dezembro de 2021↑ «The Pink Panther» (em inglês). Metacritic. Consultado em 24 de maio de 2014EstúdioDangerously in LoveB'DayI Am... Sasha Fierce4BeyoncéLemonadeEverything Is LoveAo vivoLive at WembleyThe Beyoncé Experience LiveI Am... Yours: An Intimate Performance at Wynn Las VegasI Am... World TourLive in Atlantic CityHomecoming: The Live AlbumTrilhas sonorasThe Lion King: The GiftVídeoThe Ultimate PerformerB'Day Anthology Video AlbumAbove and Beyoncé - Video CollectionLive at Roseland: Elements of 4Extended plays (

...



Pergunta 1: Quais são as configurações que o autor deseja bloquear?
Pergunta 2: Qual é o utilitário gratuito que o autor pode usar para realizar as configurações desejadas no Windows?

LLM passage queries creation duration: 2.1018285751342773; cost: 0.0012720000000000001


++++++++++++++++++++++++++
Passagem: "25 Anda na companhia do povo santo, com os que vivem e proclamam a glória de Deus. 26 Não te detenhas no erro dos ímpios, louva a Deus antes da morte; 27 após a morte nada mais há, o louvor terminou. Glorifica a Deus enquanto viveres; glorifica-o enquanto tiveres vida e saúde; louva a Deus e glorifica-o em suas misericórdias. 28 Quão grande é a misericórdia do Senhor, e o perdão que concede àqueles que para ele se voltam! 29 Pois não se pode encontrar tudo nos homens, porque os homens não são imortais, e se comprazem na vaidade e na malícia. 30 O que há de mais luminoso do que o sol? E, entretanto, ele tem eclipses. O que há de mais criminoso do que os pensamentos da carne e do



Pergunta 1: Qual é a importância da Educação Infantil?
Pergunta 2: Quais ações a Secretaria de Educação tem tomado para apoiar os alunos da Rede Municipal durante a pandemia?

LLM passage queries creation duration: 1.9232733249664307; cost: 0.0012595000000000002


++++++++++++++++++++++++++
Passagem: "Novatec EditoraQuantidade de páginas264 páginasPublicado em23 de Abril de 2017É possivel ler online?Verifique AquiLivro Entendendo Algoritmos: Um Guia Ilustrado Para Programadores e Outros Curiosos em PDFUm arquivo PDF é um documento portátil que pode ser aberto em qualquer plataforma sem que perca suas características originais. Ele é usado muitas vezes para a troca de documentos de texto (como livros, revistas, jornais) e é amplamente difundido na internet.Disponibizamos aqui no Fala, Dev! uma versão em PDF das informações gerais sobre este livro, para que você possa indicar e compartilhar com os seus amigos. Utilize o botão abaixo para salvar o arquivo compartilhável que criamos para



Pergunta 1: Como é possível carregar a conta do cartão SIGE?
Pergunta 2: Qual é o número e o formato do Pin para o primeiro acesso à plataforma Unicard SIGE pelos alunos?

LLM passage queries creation duration: 2.068619728088379; cost: 0.0012945


++++++++++++++++++++++++++
Passagem: "Testes de genética molecular (1/5)Testes de genética molecular (2/5)Testes de genética molecular (3/5)Testes de genética molecular (4/5)Testes de genética molecular (5/5)TESTES DE HERANÇA LIGADA AO SEXO (I)TESTES DE HERANÇA LIGADA AO SEXO (II)Testes de herança ligada ao sexo (1/2)Testes de herança ligada ao sexo (2/2)Testes de herança relacionada ao sexoTESTES DE HISTOLOGIA (1)TESTES DE HISTOLOGIA (2)TESTES DE HISTOLOGIA (3)TESTES DE HISTOLOGIA (4)TESTES DE HISTOLOGIA (5)Testes de histologia animalTESTES DE HISTOLOGIA ANIMAL (1)Testes de histologia animal (1/5)TESTES DE HISTOLOGIA ANIMAL (10)TESTES DE HISTOLOGIA ANIMAL (11)TESTES DE HISTOLOGIA ANIMAL (12)TESTES DE HISTOLOGIA ANIMAL (13)TESTES DE HISTOLO



Pergunta 1: Quem era Guilherme II e qual era sua relação com o bebê Guilherme?
Pergunta 2: Por que houve um conflito entre Maria e Amália de Solms-Braunfels sobre o nome do bebê?

LLM passage queries creation duration: 2.3101694583892822; cost: 0.001155


++++++++++++++++++++++++++
Passagem: "f                                                                    Capítulo 4 Instalação e Verificação do Sistema EPX-4400(4) Ligue o conector do tanque de água ao Endoscópio.4.3 Verificar o Funcionamento da Fonte LuminosaATENCAOPode causar danos à vista.Não olhe diretamente a lâmpada enquanto acesa.Não olhe diretamente a lâmpada de iluminação do Endoscópio.(1) Ligar a alimentação do Carrinho e da Fonte Luminosa.O Botão de Alimentação acenderá.(2) Confirme que está aceso o “Hi (Forte)” do indicador dofornecimento de ar.4-3f Capítulo 4 Instalação e Verificação do Sistema EPX-4400(3) Confirme o número de horas de uso da lâmpada.Quando o pictograma do número de horas de uso da lâmpadaestiver aces



Pergunta 1: O que é amor à primeira vista?
Pergunta 2: Como o amor pode ser demonstrado de formas diferentes e sutis?

LLM passage queries creation duration: 1.4385075569152832; cost: 0.0011495


train_queries_df.shape={}
 (1003, 9)


In [29]:
train_queries_df.shape

(1003, 9)

### Convert the questions to the common query format

In [30]:
train_queries_df.head()

question_theme  \
0                                     O que é essa lista?   
1  Qual foi a reação da pessoa ao abrir o aplicativo Pou?   
2                  O que são instrumentos de laboratório?   
3     Qual é o objeto do contrato mencionado na passagem?   
4                    Qual é o tema do fórum ou discussão?   

                                                                                 question_specific  \
0                                                        Qual empresa está na posição 32 da lista?   
1                                              O que aconteceu com a pessoa depois de jogar o Pou?   
2      Por que é importante que os instrumentos de laboratório sejam de alta qualidade e duráveis?   
3  Qual é o acréscimo em reais no valor total do contrato após a aplicação do reajuste contratual?   
4                   Quais são as regras de colocação para os usuários que participam da discussão?   

                                                                  usage  \
0  {'prompt_tokens': 624, 'completion_tokens': 28, 'total_tokens': 652}   
1  {'prompt_tokens': 752, 'completion_tokens': 40, 'total_tokens': 792}   
2  {'prompt_tokens': 687, 'completion_tokens': 41, 'total_tokens': 728}   
3  {'prompt_tokens': 877, 'completion_tokens': 51, 'total_tokens': 928}   
4  {'prompt_tokens': 576, 'completion_tokens': 45, 'total_tokens': 621}   

       cost  duration  \
0  0.000992  1.729614   
1  0.001208  1.563534   
2  0.001113  1.489686   
3  0.001418  2.645009   
4  0.000954  2.238307   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             passage_text  \
0        Trane Brasil - Trane Technologies........................ 70Trelleborg Sealing Solutions Brasil...................... 74TRUMPF.............................................................. 32TS Shara........................................................ 35, 56Tudor.................................................................... 10Tupy............................................................... 26, 38UUltraseal ....................................................... 50, 62Unicoba - Hikari Ferramentas................................ 4Unicoba - Unipower............................................. 10Unival............................................................ 38, 73Urano..................................................................... 9Usicorp................................................................ 30VV8 Brasil................................................................ 6Valdir Geremia..................................................... 12Vallourec.............................................................. 70Valmicro - Lupatech............................................. 72Vastec..............................................

In [32]:
theme_questions = train_queries_df['question_theme'].to_numpy()

In [34]:
specific_questions = train_queries_df['question_specific'].to_numpy()

In [35]:
theme_questions.shape

(1003,)

In [37]:
specific_questions.shape

(1003,)

In [40]:
os.getcwd()

'/mnt/0060f889-4c27-409b-b0de-47f5427515e3/unicamp/ia368v_dd/trabalho_final'

In [42]:
queries_count = 0

with open(os.path.join(CLUEWEB22_PT_TRAIN_QUERIES_FOLDER, "train_queries.tsv"), "w") as output_file:
    for i in range(train_queries_df.shape[0]):
        if queries_count > 0:
            output_file.write("\n")
            
        output_file.write("{}\t{}\n".format(queries_count, theme_questions[i]))
        queries_count += 1
        
        output_file.write("{}\t{}".format(queries_count, specific_questions[i]))
        queries_count += 1

## Now check the queries quality using BM25

### Create the BM25 searcher

In [43]:
BM25_searcher = LuceneSearcher(BM25_INDEX_FOLDER)
analyzer = get_lucene_analyzer("pt")

BM25_searcher.set_analyzer(analyzer)

### Loop through the generated questions and retrieve the related passages

In [55]:
queries_bm25_evaluation = []

for i, query in enumerate(train_queries):
    
    print("---------------------")
    
    for j, which_question in enumerate(['question_theme', 'question_specific']):
        
        if query[which_question] is not None:
            document_hits = BM25_searcher.search(query[which_question], k=1000)     

            position_found = None

            for k, document in enumerate(document_hits):
                document_dict = json.loads(document.raw)

    #             print("id: {}, score: {}".format(document_dict['id'], document.score))

                if document_dict['id'] == query['clueweb_id']:
                    position_found = k

                    break
                
        print("query_id: {}, query: {}\n-- position: {}\n".format((i * 2) + j, query[which_question], position_found))

        if query[which_question] is not None:
            queries_bm25_evaluation.append({"query_id": (i * 2) + j, "clueweb_id": query['clueweb_id'], "position": position_found})

---------------------
query_id: 0, query: O que é essa lista?
-- position: None

query_id: 1, query: Qual empresa está na posição 32 da lista?
-- position: None

---------------------
query_id: 2, query: Qual foi a reação da pessoa ao abrir o aplicativo Pou?
-- position: None

query_id: 3, query: O que aconteceu com a pessoa depois de jogar o Pou?
-- position: 493

---------------------
query_id: 4, query: O que são instrumentos de laboratório?
-- position: 0

query_id: 5, query: Por que é importante que os instrumentos de laboratório sejam de alta qualidade e duráveis?
-- position: 0

---------------------
query_id: 6, query: Qual é o objeto do contrato mencionado na passagem?
-- position: None

query_id: 7, query: Qual é o acréscimo em reais no valor total do contrato após a aplicação do reajuste contratual?
-- position: 17

---------------------
query_id: 8, query: Qual é o tema do fórum ou discussão?
-- position: None

query_id: 9, query: Quais são as regras de colocação para os us

query_id: 69, query: Quais cargos Raquel Teixeira ocupou em Goiás antes de se tornar secretária de Educação do Rio Grande do Sul?
-- position: 0

---------------------
query_id: 70, query: Como é possível mudar hábitos ruins?
-- position: None

query_id: 71, query: Quais são algumas dicas para evitar tentações e cultivar hábitos positivos?
-- position: 0

---------------------
query_id: 72, query: Quais são as diferenças entre as opiniões dos Analistas Fundamentalistas e dos Analistas Técnicos?
-- position: 103

query_id: 73, query: Qual é o perfil de investidor indicado para investir em ações e quais são os riscos envolvidos?
-- position: None

---------------------
query_id: 74, query: Quais são as vantagens de se ter um soundbar?
-- position: 0

query_id: 75, query: Por que as televisões atuais normalmente não apresentam boas configurações de áudio?
-- position: 0

---------------------
query_id: 76, query: O que é LVM e como é utilizado em algumas distribuições Linux?
-- position: 

query_id: 134, query: Qual é a forma correta de escrita da palavra que se refere a um pequeno dispositivo que produz chama?
-- position: 0

query_id: 135, query: Qual é a diferença de uso da palavra isqueiro entre o português falado no Brasil e em Portugal?
-- position: 0

---------------------
query_id: 136, query: Quais medidas cautelares podem ser aplicadas a parlamentares?
-- position: 4

query_id: 137, query: Por que não é possível aplicar multa diária como medida cautelar no processo penal?
-- position: 1

---------------------
query_id: 138, query: Como as mudanças sociais afetam a vida dos professores?
-- position: 25

query_id: 139, query: Por que a sociedade está cética em relação à educação?
-- position: None

---------------------
query_id: 140, query: O que é permitido em relação a reparos internos e substituição de aberturas em geral?
-- position: 4

query_id: 141, query: Quais são as restrições para o rebaixamento de meio-fio para acesso veicular?
-- position: 0

-------

query_id: 202, query: O que é a Síndrome de Burnout?
-- position: 473

query_id: 203, query: Como o clima organizacional pode influenciar na motivação dos colaboradores?
-- position: 35

---------------------
query_id: 204, query: Qual é a opinião do autor sobre o perfume em questão?
-- position: None

query_id: 205, query: Como o autor descreve a fragrância do perfume?
-- position: None

---------------------
query_id: 206, query: Qual é o valor da negociação para o lançamento exclusivo de Hotel Transilvânia 4?
-- position: 15

query_id: 207, query: Quais outras animações da Sony foram vendidas para o Netflix em 2021?
-- position: 6

---------------------
query_id: 208, query: Qual é o valor aproximado dos dividendos que a Enauta irá distribuir?
-- position: 0

query_id: 209, query: Por que o autor da passagem sugere que é necessário ter "um pouco de estômago" para comprar ações da Enauta?
-- position: 0

---------------------
query_id: 210, query: Qual é a função do Excel que permite

query_id: 268, query: Qual é a presunção de paternidade no caso de fecundação artificial homóloga?
-- position: 33

query_id: 269, query: Qual é a posição da doutrina brasileira em relação à reprodução póstuma?
-- position: 0

---------------------
query_id: 270, query: Quais são os principais pontos turísticos de Atlanta?
-- position: 0

query_id: 271, query: Qual é a melhor época para visitar Atlanta?
-- position: 0

---------------------
query_id: 272, query: Qual é o título do filme mencionado na passagem?
-- position: None

query_id: 273, query: Quais são os diferentes portais e bancos de dados que mencionam o filme "The Adventures of Rocky and Bullwinkle"?
-- position: 61

---------------------
query_id: 274, query: Qual foi a tendência criada por Sugar Minott no final dos anos 60?
-- position: 0

query_id: 275, query: Quais foram os cantores que emergiram como grandes astros no início da era do dancehall?
-- position: 0

---------------------
query_id: 276, query: Como um estagi

...

query_id: 1672, query: Qual é a função da pessoa responsável pela Secretaria mencionada na passagem?
-- position: None

query_id: 1673, query: O que é esperado da pessoa responsável pela Secretaria em relação ao patrimônio alocado na unidade?
-- position: 0

---------------------
query_id: 1674, query: O que são os Objetivos de Desenvolvimento Sustentável?
-- position: 305

query_id: 1675, query: Como os governos podem definir suas próprias metas em relação aos Objetivos de Desenvolvimento Sustentável?
-- position: 2

---------------------
query_id: 1676, query: Qual é a data de estreia do Big Brother - Duplo Impacto e quem serão os apresentadores?
-- position: 2

query_id: 1677, query: Quais ex-concorrentes do BB2020 estarão presentes no Big Brother - Duplo Impacto?
-- position: 0

---------------------
query_id: 1678, query: Quais foram as chapas que concorreram nas eleições indiretas de 1985?
-- position: 1

query_id: 1679, query: Qual foi o resultado das eleições indiretas de 1985 

query_id: 1738, query: Qual é a opinião do autor sobre o Novo Ford Focus 1.0 EcoBoost?
-- position: 0

query_id: 1739, query: Quais são os pontos fortes e pontos menos favoráveis do carro mencionados na passagem?
-- position: 1

---------------------
query_id: 1740, query: Qual é o papel dos movimentos sociais na luta pelos direitos humanos?
-- position: 3

query_id: 1741, query: Como os direitos culturais estão relacionados aos direitos humanos?
-- position: 562

---------------------
query_id: 1742, query: Qual é o valor que a Band deve lucrar com a estreia do programa de Faustão?
-- position: 0

query_id: 1743, query: Quais ex-Globais podem aparecer no novo programa de Faustão na Band?
-- position: 0

---------------------
query_id: 1744, query: Como as nuvens são formadas?
-- position: 86

query_id: 1745, query: Quais são os tipos de nuvens e como são classificadas?
-- position: 862

---------------------
query_id: 1746, query: Qual é o tema principal dos arquivos mencionados na pa

query_id: 1805, query: Quais são as especializações oferecidas no sistema tradicional segundo ensinamentos do Guru Swami Sivananda?
-- position: 5

---------------------
query_id: 1806, query: Por que parar para pensar pode levar a uma transferência de faculdade?
-- position: 0

query_id: 1807, query: O que é abordado no material "Começou a facul e não gostou? Transferência de faculdade pode ser uma opção"?
-- position: 0

---------------------
query_id: 1808, query: Qual setor do varejo foi menos afetado pela crise e pela pandemia?
-- position: 9

query_id: 1809, query: Quantas lojas a rede de franquia Pinta Mundi Tintas tinha no final de 2019 e quantas pretende ter até o final deste ano?
-- position: 0

---------------------
query_id: 1810, query: Qual é o software necessário para fazer a assinatura?
-- position: None

query_id: 1811, query: Qual é o endereço de e-mail para envio do documento assinado?
-- position: None

---------------------
query_id: 1812, query: O que é a Súmula 4

query_id: 1871, query: Quais são as características predominantes do movimento Barroco?
-- position: 1

---------------------
query_id: 1872, query: Quais medicamentos podem aumentar a exposição à fentanila?
-- position: 2

query_id: 1873, query: Qual é a recomendação para pacientes em uso de inibidores da MAO antes de receberem Fentanil®?
-- position: 0

---------------------
query_id: 1874, query: Quais são as certidões que podem ser fornecidas pelo 2º Tabelionato de Protestos de Centro, Porto Alegre?
-- position: 1

query_id: 1875, query: Qual é o horário de funcionamento do cartório e como é possível confirmar o expediente no sábado?
-- position: 53

---------------------
query_id: 1876, query: O que é resolução em relação a displays?
-- position: 81

query_id: 1877, query: Qual é a importância da taxa de atualização em um display?
-- position: None

---------------------
query_id: 1878, query: Quais são as restrições para a utilização de recursos do FGTS na compra de um imóvel?
--

query_id: 1937, query: Qual é o código que deve ser informado para vendas de unidades pelo PMCMV de 1% e 4% na DCTF?
-- position: 0

---------------------
query_id: 1938, query: Quais são as melhores corretoras de Forex?
-- position: 77

query_id: 1939, query: Por que é importante pesquisar antes de escolher uma corretora de Forex?
-- position: 0

---------------------
query_id: 1940, query: Qual é a sugestão do autor para o WhatsApp?
-- position: None

query_id: 1941, query: O que são os truques legais mencionados no texto para usar no WhatsApp?
-- position: 5

---------------------
query_id: 1942, query: Qual é o objetivo da tabela apresentada no texto?
-- position: None

query_id: 1943, query: Qual é o grau do adjetivo presente na frase "A menina colheu a flor mais bela do jardim"?
-- position: 0

---------------------
query_id: 1944, query: Como baixar um vídeo do YouTube usando o Snappea?
-- position: 42

query_id: 1945, query: Quais são as vantagens de usar o Snappea para baixar 

In [56]:
len(queries_bm25_evaluation)

2004

In [57]:
queries_bm25_evaluation_df = pd.DataFrame(queries_bm25_evaluation)

In [58]:
queries_bm25_evaluation_df

query_id                     clueweb_id  position
0            0  clueweb22-pt0000-98-03152_171       NaN
1            1  clueweb22-pt0000-98-03152_171       NaN
2            2    clueweb22-pt0001-21-17058_2       NaN
3            3    clueweb22-pt0001-21-17058_2     493.0
4            4    clueweb22-pt0000-99-15136_0       0.0
...        ...                            ...       ...
1999      2001    clueweb22-pt0000-33-21046_4       0.0
2000      2002   clueweb22-pt0000-71-06569_23       3.0
2001      2003   clueweb22-pt0000-71-06569_23       0.0
2002      2004    clueweb22-pt0000-81-11468_4     107.0
2003      2005    clueweb22-pt0000-81-11468_4       5.0

[2004 rows x 3 columns]

In [60]:
queries_bm25_evaluation_df.to_csv(os.path.join(CLUEWEB22_PT_TRAIN_QUERIES_FOLDER, "train_queries_bm25_filter.tsv"), sep="\t", index=False)